In [ ]:
import pandas as pd
import os
from easynmt import EasyNMT


In [ ]:
URL_BASE = "https://arxiv.org/pdf/"
PDF_PATH = 'PDF'
TXT_PATH= 'TXT'
CSV_PATH = 'CSV'

# Get Data from TXT

In [ ]:
data = pd.read_json('ARxiv/arxiv-metadata-oai-snapshot.json',lines=True, chunksize=2001,dtype={'id':'str'})
df = None
for i in data:
    df = i 
    print(type(i))
    break
df = df[['id','title','abstract']]


In [ ]:
for file in df['id']:
    file_path = TXT_PATH+'/'+str(file)+'.pdf.txt'
    if  os.path.isfile(file_path):
        with open(file_path,'r',encoding='utf8') as f:
            s =str( f.read()) 
            df.loc[df['id'] == str(file),'full_text'] = s          

In [ ]:
df = df.dropna()
df.reset_index()
df.to_csv(CSV_PATH+'/scientific_paper_en.csv',index=False,encoding='utf-8')
df

# first run 


In [ ]:
df = pd.read_csv(CSV_PATH +'/scientific_paper_en.csv',dtype={'id':'str'})
df.to_csv(CSV_PATH+'/scientific_paper_full_text_translated.csv',index=False,encoding='utf-8')

# leer datos

In [ ]:
df = pd.read_csv(CSV_PATH +'/scientific_paper_full_text_translated.csv',dtype={'id':'str'})
print(len(df.index))
df

# translate

In [ ]:
model = EasyNMT('opus-mt')

## translate full text

In [ ]:
max = len(df.index)
for i in range(0,1754):
    text = df.iloc[i]['full_text']
    translated_text = model.translate(text, target_lang='es')
    df.loc[i,'translated'] = translated_text   
    print("listo documento ",i)
    if(i%10==0):
        df.to_csv(CSV_PATH+'/scientific_paper_full_text_translated.csv',index=False,encoding='utf-8')
df.to_csv(CSV_PATH+'/scientific_paper_full_text_translated.csv',index=False,encoding='utf-8')

## translate abstract

In [ ]:
max = len(df.index)
for i in range(0,1754):
    text = df.iloc[i]['abstract']
    translated_text = model.translate(text, target_lang='es')
    df.loc[i,'translated_abstract'] = translated_text   
    print("listo documento ",i)
    if(i%100==0):
        df.to_csv(CSV_PATH+'/scientific_paper_full_text_translated.csv',index=False,encoding='utf-8')
df.to_csv(CSV_PATH+'/scientific_paper_full_text_translated.csv',index=False,encoding='utf-8')



# remove abstract

In [ ]:
max = len(df.index)-1

In [ ]:
end = 'Introducción'
for i in range(0,max):
    text = df.iloc[i]['translated']    
    p = text.find(end)
    if(p != -1):        
        df.loc[i,'translated_no_abstract'] = text[p:]   
    else:
        df.loc[i,'translated_no_abstract']= text
    print("listo documento ",i,p)
    if(i%1000==0):
        df.to_csv(CSV_PATH+'/scientific_paper_full_text_translated.csv',index=False,encoding='utf-8')
df.to_csv(CSV_PATH+'/scientific_paper_full_text_translated.csv',index=False,encoding='utf-8')

In [ ]:
end = 'Abstract'
for i in range(0,max):
    text = df.iloc[i]['full_text']    
    p = text.find(end)
    if(p != -1):        
        df.loc[i,'text_no_abstract'] = text[p:]   
    else:
        df.loc[i,'text_no_abstract']= text    
    if(i%1000==0):
        df.to_csv(CSV_PATH+'/scientific_paper_full_text_translated.csv',index=False,encoding='utf-8')
df.to_csv(CSV_PATH+'/scientific_paper_full_text_translated.csv',index=False,encoding='utf-8')

# split data to csv

In [ ]:
df = pd.read_csv(CSV_PATH +'/scientific_paper_full_text_translated.csv',dtype={'id':'str'})
df

In [77]:
es = df[['id','title','translated','translated_abstract','translated_no_abstract']]
es.columns = ["id","title", "full_text","abstract","text_no_abstract"]
es.to_csv(CSV_PATH+'/scientific_paper_es.csv',index=False,encoding='utf-8')
es

id                                              title  \
0     0704.0002           Sparsity-certifying Graph Decompositions   
1     0704.0003  The evolution of the Earth-Moon system based o...   
2     0704.0004  A determinant of Stirling cycle numbers counts...   
3     0704.0005  From dyadic $\Lambda_{\alpha}$ to $\Lambda_{\a...   
4     0704.0007  Polymer Quantum Mechanics and its Continuum Limit   
...         ...                                                ...   
1749  0704.1996              A Wave-function for Stringy Universes   
1750  0704.1997  Query on Negative Temperature, Internal Intera...   
1751  0704.1998  Absence of the Fifth Force Problem in a Model ...   
1752  0704.1999  Dark matter caustics and the enhancement of se...   
1753  0704.2000  Search for a Higgs boson produced in associati...   

                                              full_text  \
0     Descomposiciones del gráfico de certificación ...   
1     La evolución del sistema Tierra-Luna basado en...   
2     Un determinante de los números de ciclo de Sti...   
3     DE DÍA A DÍA\nWAEL ABU-SHAMMALA Y ALBERTO TORC...   
4     La mecánica cuántica de polímeros y su límite ...   
...                                                 ...   
1749  LPTENS–07/16\nAbril de 2007\nUna función de on...   
1750  Microsoft Word - negEntr.doc\nConsulta sobre t...   
1751  Ausencia del problema de la quinta fuerza en u...   
1752  Proyecto de versión 16 de noviembre de 2018\nT...   
1753  FERMILAB-PUB-07/076-E\nBúsqueda de un bosón Hi...   

                                               abstract  \
0       Describimos un nuevo algoritmo, el juego de ...   
1       La evolución del sistema Tierra-Luna es desc...   
2       Demostramos que un determinante de los númer...   
3       En este artículo mostramos cómo calcular la ...   
4       Una representación cuántica no estándar de l...   
...                                                 ...   
1749    Definimos una función de onda para los fondo...   
1750    Después de que la temperatura negativa se vu...   
1751    Un modelo de escala invariante que contiene ...   
1752    Los haloes fríos de materia oscura están pob...   
1753    Describimos una búsqueda para el modelo está...   

                                       text_no_abstract  
0     Introducción y preliminares\nEl foco de este d...  
1     Introducción \nLa teoría aceptada popularmente...  
2     Introducción El propósito principal de este ar...  
3     DE DÍA A DÍA\nWAEL ABU-SHAMMALA Y ALBERTO TORC...  
4     La mecánica cuántica de polímeros y su límite ...  
...                                                 ...  
1749  Introducción\nNuestro objetivo en este documen...  
1750  Microsoft Word - negEntr.doc\nConsulta sobre t...  
1751  Introducción\n\tBase de Dos Medidas Teoría de ...  
1752  Proyecto de versión 16 de noviembre de 2018\nT...  
1753  FERMILAB-PUB-07/076-E\nBúsqueda de un bosón Hi...  

[1754 rows x 5 columns]

In [79]:
en = df[['id','title','full_text','abstract','text_no_abstract']]
en.columns = ["id","title", "full_text","abstract","text_no_abstract"]
en.to_csv(CSV_PATH+'/scientific_paper_en.csv',index=False,encoding='utf-8')
en

id                                              title  \
0     0704.0002           Sparsity-certifying Graph Decompositions   
1     0704.0003  The evolution of the Earth-Moon system based o...   
2     0704.0004  A determinant of Stirling cycle numbers counts...   
3     0704.0005  From dyadic $\Lambda_{\alpha}$ to $\Lambda_{\a...   
4     0704.0007  Polymer Quantum Mechanics and its Continuum Limit   
...         ...                                                ...   
1749  0704.1996              A Wave-function for Stringy Universes   
1750  0704.1997  Query on Negative Temperature, Internal Intera...   
1751  0704.1998  Absence of the Fifth Force Problem in a Model ...   
1752  0704.1999  Dark matter caustics and the enhancement of se...   
1753  0704.2000  Search for a Higgs boson produced in associati...   

                                              full_text  \
0     Sparsity-certifying Graph Decompositions\nIlea...   
1     The evolution of the Earth-Moon system based o...   
2     A Determinant of Stirling Cycle Numbers Counts...   
3     FROM DYADIC Λα TO Λα\nWAEL ABU-SHAMMALA AND AL...   
4     Polymer Quantum Mechanics and its Continuum Li...   
...                                                 ...   
1749  LPTENS–07/16\nApril 2007\nA Wave-function for ...   
1750  Microsoft Word - negEntr.doc\nQuery on Negativ...   
1751  Absence of the Fifth Force Problem in a Model ...   
1752  Draft version November 16, 2018\nPreprint type...   
1753  FERMILAB-PUB-07/076-E\nSearch for a Higgs boso...   

                                               abstract  \
0       We describe a new algorithm, the $(k,\ell)$-...   
1       The evolution of Earth-Moon system is descri...   
2       We show that a determinant of Stirling cycle...   
3       In this paper we show how to compute the $\L...   
4       A rather non-standard quantum representation...   
...                                                 ...   
1749    We define a wave-function for string theory ...   
1750    After negative temperature is restated, we f...   
1751    A scale invariant model containing dilaton $...   
1752    Cold dark matter haloes are populated by cau...   
1753    We describe a search for the standard model ...   

                                       text_no_abstract  
0     Introduction and preliminaries\nThe focus of t...  
1     Introduction \nThe popularly accepted theory f...  
2     Introduction The chief purpose of this paper i...  
3     FROM DYADIC Λα TO Λα\nWAEL ABU-SHAMMALA AND AL...  
4     Polymer Quantum Mechanics and its Continuum Li...  
...                                                 ...  
1749  Introduction\nOur goal in this paper is to emb...  
1750  Microsoft Word - negEntr.doc\nQuery on Negativ...  
1751  Introduction\n\tBasis of Two Measures Field Th...  
1752  Draft version November 16, 2018\nPreprint type...  
1753  FERMILAB-PUB-07/076-E\nSearch for a Higgs boso...  

[1754 rows x 5 columns]